# Machine Learning Intro - Python

First, we import the packages we need:

In [17]:
from scipy.io import arff # to read arff files
import pandas as pd # for data manipulation
import numpy as np
from sklearn.neural_network import MLPClassifier
from sklearn import preprocessing, svm
from sklearn.feature_selection import SelectKBest
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.pipeline import Pipeline
from sklearn.model_selection import StratifiedKFold, RandomizedSearchCV
from sklearn.metrics import make_scorer, accuracy_score, precision_score, recall_score, classification_report, confusion_matrix, roc_curve, auc, roc_auc_score

Now, we load the data set into a dataframe and display the first few rows:

In [18]:
# load dataset (arff file)
data = arff.loadarff('diabetes.arff')

# transform into a dataframe
df = pd.DataFrame(data[0])

# decode the class label from a byte object into a string with utf-8 encoding
df['class'] = df['class'].str.decode('utf-8')

#display the first 5 rows
df.head(30)

preg   plas  pres  skin   insu  mass   pedi   age            class
0    6.0  148.0  72.0  35.0    0.0  33.6  0.627  50.0  tested_positive
1    1.0   85.0  66.0  29.0    0.0  26.6  0.351  31.0  tested_negative
2    8.0  183.0  64.0   0.0    0.0  23.3  0.672  32.0  tested_positive
3    1.0   89.0  66.0  23.0   94.0  28.1  0.167  21.0  tested_negative
4    0.0  137.0  40.0  35.0  168.0  43.1  2.288  33.0  tested_positive
5    5.0  116.0  74.0   0.0    0.0  25.6  0.201  30.0  tested_negative
6    3.0   78.0  50.0  32.0   88.0  31.0  0.248  26.0  tested_positive
7   10.0  115.0   0.0   0.0    0.0  35.3  0.134  29.0  tested_negative
8    2.0  197.0  70.0  45.0  543.0  30.5  0.158  53.0  tested_positive
9    8.0  125.0  96.0   0.0    0.0   0.0  0.232  54.0  tested_positive
10   4.0  110.0  92.0   0.0    0.0  37.6  0.191  30.0  tested_negative
11  10.0  168.0  74.0   0.0    0.0  38.0  0.537  34.0  tested_positive
12  10.0  139.0  80.0   0.0    0.0  27.1  1.441  57.0  tested_negative
13   1.0  189.0  60.0  23.0  846.0  30.1  0.398  59.0  tested_positive
14   5.0  166.0  72.0  19.0  175.0  25.8  0.587  51.0  tested_positive
15   7.0  100.0   0.0   0.0    0.0  30.0  0.484  32.0  tested_positive
16   0.0  118.0  84.0  47.0  230.0  45.8  0.551  31.0  tested_positive
17   7.0  107.0  74.0   0.0    0.0  29.6  0.254  31.0  tested_positive
18   1.0  103.0  30.0  38.0   83.0  43.3  0.183  33.0  tested_negative
19   1.0  115.0  70.0  30.0   96.0  34.6  0.529  32.0  tested_positive
20   3.0  126.0  88.0  41.0  235.0  39.3  0.704  27.0  tested_negative
21   8.0   99.0  84.0   0.0    0.0  35.4  0.388  50.0  tested_negative
22   7.0  196.0  90.0   0.0    0.0  39.8  0.451  41.0  tested_positive
23   9.0  119.0  80.0  35.0    0.0  29.0  0.263  29.0  tested_positive
24  11.0  143.0  94.0  33.0  146.0  36.6  0.254  51.0  tested_positive
25  10.0  125.0  70.0  26.0  115.0  31.1  0.205  41.0  tested_positive
26   7.0  147.0  76.0   0.0    0.0  39.4  0.257  43.0  tested_positive
27   1.0   97.0  66.0  15.0  140.0  23.2  0.487  22.0  tested_negative
28  13.0  145.0  82.0  19.0  110.0  22.2  0.245  57.0  tested_negative
29   5.0  117.0  92.0   0.0    0.0  34.1  0.337  38.0  tested_negative

As a first step, we could explore the dataset:

In [19]:
df.describe()

preg        plas        pres        skin        insu        mass  \
count  768.000000  768.000000  768.000000  768.000000  768.000000  768.000000   
mean     3.845052  120.894531   69.105469   20.536458   79.799479   31.992578   
std      3.369578   31.972618   19.355807   15.952218  115.244002    7.884160   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      1.000000   99.000000   62.000000    0.000000    0.000000   27.300000   
50%      3.000000  117.000000   72.000000   23.000000   30.500000   32.000000   
75%      6.000000  140.250000   80.000000   32.000000  127.250000   36.600000   
max     17.000000  199.000000  122.000000   99.000000  846.000000   67.100000   

             pedi         age  
count  768.000000  768.000000  
mean     0.471876   33.240885  
std      0.331329   11.760232  
min      0.078000   21.000000  
25%      0.243750   24.000000  
50%      0.372500   29.000000  
75%      0.626250   41.000000  
max      2.420000   81.000000

In [20]:
# how many samples do we have per class?

display('Number of positive samples:')
nr_pos_samples = df[df['class'] == 'tested_positive']['class'].count()
display(nr_pos_samples)

display('Number of negative samples:')
nr_neg_samples = df[df['class'] == 'tested_negative']['class'].count()
display(nr_neg_samples)

display('Percentage of positive samples:')
display((nr_pos_samples / df['class'].count()) * 100)

'Number of positive samples:'

268

'Number of negative samples:'

500

'Percentage of positive samples:'

34.89583333333333

Preprocessing: Are there missing values? Do you need to transform data (e.g. dates, ...)?

In this case, we mark zero values as missing values, since we assume that a value of exactly 0 is not a valid measurement.

In [21]:
# mark missing values as NaN
df = df.replace(0, np.NaN)
df.head(30)

preg   plas  pres  skin   insu  mass   pedi   age            class
0    6.0  148.0  72.0  35.0    NaN  33.6  0.627  50.0  tested_positive
1    1.0   85.0  66.0  29.0    NaN  26.6  0.351  31.0  tested_negative
2    8.0  183.0  64.0   NaN    NaN  23.3  0.672  32.0  tested_positive
3    1.0   89.0  66.0  23.0   94.0  28.1  0.167  21.0  tested_negative
4    NaN  137.0  40.0  35.0  168.0  43.1  2.288  33.0  tested_positive
5    5.0  116.0  74.0   NaN    NaN  25.6  0.201  30.0  tested_negative
6    3.0   78.0  50.0  32.0   88.0  31.0  0.248  26.0  tested_positive
7   10.0  115.0   NaN   NaN    NaN  35.3  0.134  29.0  tested_negative
8    2.0  197.0  70.0  45.0  543.0  30.5  0.158  53.0  tested_positive
9    8.0  125.0  96.0   NaN    NaN   NaN  0.232  54.0  tested_positive
10   4.0  110.0  92.0   NaN    NaN  37.6  0.191  30.0  tested_negative
11  10.0  168.0  74.0   NaN    NaN  38.0  0.537  34.0  tested_positive
12  10.0  139.0  80.0   NaN    NaN  27.1  1.441  57.0  tested_negative
13   1.0  189.0  60.0  23.0  846.0  30.1  0.398  59.0  tested_positive
14   5.0  166.0  72.0  19.0  175.0  25.8  0.587  51.0  tested_positive
15   7.0  100.0   NaN   NaN    NaN  30.0  0.484  32.0  tested_positive
16   NaN  118.0  84.0  47.0  230.0  45.8  0.551  31.0  tested_positive
17   7.0  107.0  74.0   NaN    NaN  29.6  0.254  31.0  tested_positive
18   1.0  103.0  30.0  38.0   83.0  43.3  0.183  33.0  tested_negative
19   1.0  115.0  70.0  30.0   96.0  34.6  0.529  32.0  tested_positive
20   3.0  126.0  88.0  41.0  235.0  39.3  0.704  27.0  tested_negative
21   8.0   99.0  84.0   NaN    NaN  35.4  0.388  50.0  tested_negative
22   7.0  196.0  90.0   NaN    NaN  39.8  0.451  41.0  tested_positive
23   9.0  119.0  80.0  35.0    NaN  29.0  0.263  29.0  tested_positive
24  11.0  143.0  94.0  33.0  146.0  36.6  0.254  51.0  tested_positive
25  10.0  125.0  70.0  26.0  115.0  31.1  0.205  41.0  tested_positive
26   7.0  147.0  76.0   NaN    NaN  39.4  0.257  43.0  tested_positive
27   1.0   97.0  66.0  15.0  140.0  23.2  0.487  22.0  tested_negative
28  13.0  145.0  82.0  19.0  110.0  22.2  0.245  57.0  tested_negative
29   5.0  117.0  92.0   NaN    NaN  34.1  0.337  38.0  tested_negative

Now we want to run machine learning, and we define several classifier pipelines that we want to try out.

The classifier pipeline have various possibilities for configuring. Here we try out:
* Imputation: This preprocessing step replaces missing values with a value, in this case with the mean. This usually improves the performance of the classifier. There are several possibilities to deal with missing values. https://machinelearningmastery.com/handle-missing-data-python/
* Scaling: The standard scales normalizes the features, such that each feature's values are distributed between -1 and +1. This helps to prevent that a certain features is weighted more only because it has larger values than another one.
* Feature Selection: only use a subset of the features compared to all
* Classifiers: try out different classifiers

In [22]:
# define classifiers and parameters to evaluate
steps_decision_forest = [
    ("imputation", preprocessing.Imputer(missing_values='NaN', strategy='mean', axis=0)),
    ("scaling", preprocessing.StandardScaler()),
    ("feature_selection", SelectKBest()),
    ("classifier", RandomForestClassifier(n_estimators = 500))
]

parameters_decision_forest = dict(
    feature_selection__k = [2, 4, 6, 'all'],
    classifier__n_estimators = [100, 250, 500, 1000],
    classifier__max_features = ["sqrt", "log2", 0.25, 0.5],
    classifier__min_samples_leaf = [5, 10, 30, 50]
)

steps_gradient_boost = [
    ("imputation", preprocessing.Imputer(missing_values='NaN', strategy='mean', axis=0)),
    ("scaling", preprocessing.StandardScaler()),
    ("feature_selection", SelectKBest()),
    ("classifier", GradientBoostingClassifier(n_estimators = 500))
]

parameters_gradient_boost = dict(
    feature_selection__k = [2, 4, 6, 'all'],
    classifier__n_estimators = [100, 250, 500, 1000],
    classifier__loss = ["deviance", "exponential"],
    classifier__learning_rate = [0.05, 0.1, 0.15],
    classifier__max_features = ["sqrt", "log2", 0.25, 0.5],
    classifier__min_samples_leaf = [5, 10, 30, 50]
)

steps_svm = [
    ("imputation", preprocessing.Imputer(missing_values='NaN', strategy='mean', axis=0)),
    ("scaling", preprocessing.StandardScaler()),
    ("feature_selection", SelectKBest(k=30)),
    ("classifier", svm.SVC(kernel="rbf"))
]

parameters_svm = dict(
    feature_selection__k = [2, 4, 6, 'all'],
    classifier__kernel = ["rbf", "linear", "poly", "sigmoid"],
    classifier__C = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10],
    classifier__gamma = [0.01, 0.02, 0.03, 0.04, 0.05, 0.10, 0.2, 0.3, 0.4, 0.5]
)

steps_neural_network = [
    ("imputation", preprocessing.Imputer(missing_values='NaN', strategy='mean', axis=0)),
    ("scaling", preprocessing.StandardScaler()),
    ("feature_selection", SelectKBest()),
    ("classifier", MLPClassifier(solver="lbfgs"))
]

parameters_neural_network = dict(
    feature_selection__k = [2, 4, 6, 8, 'all'],
    classifier__solver = ["lbfgs", "sgd"],
    classifier__alpha = [0.00001, 0.0001, 0.001, 0.01, 1],
    classifier__activation = ["identity", "logistic", "tanh", "relu"],
    classifier__learning_rate = ["constant", "invscaling", "adaptive"]
)

steps_naive_bayes = [
    ("imputation", preprocessing.Imputer(missing_values='NaN', strategy='mean', axis=0)),
    ("scaling", preprocessing.StandardScaler()),
    ("feature_selection", SelectKBest(k=30)),
    ("classifier", GaussianNB())
]

parameters_naive_bayes =  dict(
    feature_selection__k = [2, 4, 6, 8, 'all']
)

# all our classifiers with parameters
pipelines = [(steps_decision_forest, parameters_decision_forest),
             (steps_gradient_boost, parameters_gradient_boost),
             (steps_svm, parameters_svm),
             (steps_neural_network, parameters_neural_network),
             (steps_naive_bayes, parameters_naive_bayes)]

Predict the class value for each pipeline and print out the results:

In [23]:
# split into training/test set
stratifiedFolds = StratifiedKFold(n_splits=3, shuffle=True)

X = df.drop(columns=["class"]).values
y = df["class"].values

for steps in pipelines:
    pipeline = Pipeline(steps[0])
    parameters = steps[1]
    display("Classifier: ", pipeline.named_steps.classifier)

    numTrials = 3
    accuracies = []
    weighted_precisions = []
    weighted_recalls = []
    precisions_positive = []
    precisions_negative = []
    recalls_positive = []
    recalls_negative = []

    totals_originalclass = []
    totals_predictedclass = []  

    for i in range(numTrials):
        display("Starting Trial " + str(i))
        originalclass = []
        predictedclass = []

        for train_index, test_index in stratifiedFolds.split(X, y):
            # Need to specify the positive label here as the default metric auc_roc only works for binary label.
            #def custom_auc(ground_truth, predictions):
            #    fpr, tpr, _ = roc_curve(ground_truth, predictions[:, 1], pos_label='Switch')
            #    return auc(fpr, tpr)

            #roc_auc_scorer = make_scorer(custom_auc, greater_is_better=True, needs_proba=True)

            randomSearch = RandomizedSearchCV(pipeline, parameters, cv=5, scoring=None, n_iter=5)
            randomSearch.fit(X[train_index], y=y[train_index])
            print("Best parameters: ", randomSearch.best_params_)

            y_pred = randomSearch.predict(X[test_index])
            originalclass.extend(y[test_index])
            predictedclass.extend(y_pred)
            totals_originalclass.extend(y[test_index])
            totals_predictedclass.extend(y_pred)

        # after each complete trial, store results
        trial_accuracy = accuracy_score(originalclass, predictedclass)
        accuracies.extend([trial_accuracy])

        trial_weighted_precision = precision_score(originalclass, predictedclass, average="weighted")
        weighted_precisions.extend([trial_weighted_precision])
        trial_precision_positive = precision_score(originalclass, predictedclass, average="binary", pos_label="tested_positive")
        precisions_positive.extend([trial_precision_positive])
        trial_precision_negative = precision_score(originalclass, predictedclass, average="binary", pos_label="tested_negative")
        precisions_negative.extend([trial_precision_negative])

        trial_weighted_recall = recall_score(originalclass, predictedclass, average="weighted")
        weighted_recalls.extend([trial_weighted_recall])
        trial_recall_positive = recall_score(originalclass, predictedclass, average="binary", pos_label="tested_positive")
        recalls_positive.extend([trial_recall_positive])
        trial_recall_negative = recall_score(originalclass, predictedclass, average="binary", pos_label="tested_negative")
        recalls_negative.extend([trial_recall_negative])

    display('Scores of classification:')
    display("Classifier: " + str(pipeline.named_steps.classifier))
    display("Accuracy: " + str(np.mean(accuracies)) + " +/- " + str(np.std(accuracies)))
    display("Weighted Precision: " + str(np.mean(weighted_precisions)) + " +/- " + str(np.std(weighted_precisions)))
    display("Weighted Recall: " + str(np.mean(weighted_recalls)) + " +/- " + str(np.std(weighted_recalls)))
    display("Precision Tested Positive: " + str(np.mean(precisions_positive)) + " +/- " + str(np.std(precisions_positive)))
    display("Precision Tested Negative: " + str(np.mean(precisions_negative)) + " +/- " + str(np.std(precisions_negative)))
    display("Recall Tested Positive: " + str(np.mean(recalls_positive)) + " +/- " + str(np.std(recalls_positive)))
    display("Recall Tested Negative: " + str(np.mean(recalls_negative)) + " +/- " + str(np.std(recalls_negative)))
    conf_matrix = confusion_matrix(totals_originalclass, totals_predictedclass) / numTrials
    display("Confusion Matrix: ")
    display(conf_matrix)

'Classifier: '

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=500, n_jobs=1,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False)

'Starting Trial 0'

Best parameters:  {'feature_selection__k': 4, 'classifier__n_estimators': 1000, 'classifier__min_samples_leaf': 50, 'classifier__max_features': 'log2'}
Best parameters:  {'feature_selection__k': 2, 'classifier__n_estimators': 500, 'classifier__min_samples_leaf': 30, 'classifier__max_features': 'log2'}
Best parameters:  {'feature_selection__k': 4, 'classifier__n_estimators': 1000, 'classifier__min_samples_leaf': 50, 'classifier__max_features': 'log2'}


'Starting Trial 1'

...

'Precision Tested Negative: 0.7837703632820575 +/- 0.0024749828971138833'

'Recall Tested Positive: 0.5621890547263683 +/- 0.0046538027198680795'

'Recall Tested Negative: 0.8506666666666667 +/- 0.010370899457402705'

'Confusion Matrix: '

array([[425.33333333,  74.66666667],
       [117.33333333, 150.66666667]])